##  Standard Odometry model

| ![odometry](https://www.mrpt.org/wp-content/uploads/2010/08/Motion_model_thrun.png) |
| :--: | 
| *www.mrpt.org* |


$$ u = (\delta_{rot1}, \delta_{trans}, \delta_{rot2}) $$

$$
\begin{pmatrix}
x' \\
y' \\
\theta' \\
\end{pmatrix}
= 
\begin{pmatrix}
x \\
y \\
\theta \\
\end{pmatrix}
+
\begin{pmatrix}
  \delta_{trans} \cos(\theta + \delta_{rot1}) \\
  \delta_{trans} \sin(\theta + \delta_{rot1}) \\
  \delta_{rot1} + \delta_{rot2}
\end{pmatrix}
$$

In [ ]:
struct Odometry
    rot1::Float32
    trans::Float32
    rot2::Float32
end

function standard_odometry_model(pose, odometry)
    x, y, θ = pose
    direction = θ + odometry.rot1
    x += odometry.trans * cos(direction)
    y += odometry.trans * sin(direction)
    θ += odometry.rot1 + odometry.rot2
    θ = rem2pi(θ, RoundNearest)  # Round to [-π, π]
    return [x, y, θ]
end

## Range-bearing RangeBearing

$$z_t^i = (r_t^i, \phi_t^i)^T$$

$$
\begin{pmatrix}
\bar \mu_{j,x} \\
\bar \mu_{j,y} \\
\end{pmatrix}
=
\begin{pmatrix}
\bar \mu_{t,x} \\
\bar \mu_{t,y} \\
\end{pmatrix}
+
\begin{pmatrix}
r_t^i \cos(\phi_t^i + \bar \mu_{t, \theta}) \\
r_t^i \sin(\phi_t^i + \bar \mu_{t, \theta}) \\
\end{pmatrix}
$$

In [ ]:
struct RangeBearing
    landmark_id::Int8
    range::Float32
    bearing::Float32
end

function range_bearing_model(robot_pose, RangeBearing)
    x, y, θ = robot_pose
    mx = x + RangeBearing.range * cos(RangeBearing.bearing + θ)
    my = y + RangeBearing.range * sin(RangeBearing.bearing + θ)
    return [mx, my]
end

## State representation

State represents an estimation (belief) of the robot's pose $(x,y,\theta)$ and locations of n landmarks:

$$ x_t = (x, y, \theta, m_{1,x}, m_{1,y}, \dots, m_{n, x}, m_{n, y}) $$

In [ ]:
mutable struct Belief
    μ::Array{Float32,1}
    Σ::Array{Float32,2}
end

# Initialization
n = 9
μ = zeros(Float32, 2n+3)
Σ = ones(Float32, 2n+3, 2n+3)

belief=Belief(μ, Σ)

## Prediction step

In [ ]:
function prediction_step(belief, odometry)
    # Compute the new mu based on the noise-free (odometry-based) motion model
    rx, ry, rθ = belief.mean[1:3]
    belief.mean[1:3] = standard_odometry_model([rx, ry, rθ], odometry)

    # Compute the 3x3 Jacobian Gx of the motion model
    Gx = Matrix{Float32}(I, 3, 3)
    heading = rθ + odometry.rot1
    Gx[1, 3] -= odometry.trans * sin(heading)  # ∂x'/∂θ
    Gx[2, 3] += odometry.trans * cos(heading)  # ∂y'/∂θ

    # Motion noise
    Rx = Diagonal{Float32}([0.1, 0.1, 0.01])

    # Compute the predicted sigma after incorporating the motion
    Σxx = belief.covariance[1:3, 1:3]
    Σxm = belief.covariance[1:3, 4:end]

    Σ = Matrix(belief.covariance)
    Σ[1:3, 1:3] = Gx * Σxx * Gx' + Rx
    Σ[1:3, 4:end] = Gx * Σxm
    belief.covariance = Symmetric(Σ)

end

## Correction step

In [ ]:
function correction_step(belief, range_bearings)
	rx, ry, rθ = belief.mean[1:3]

	num_range_bearings = length(range_bearings)
	num_dim_state = length(belief.mean)

	H = Matrix{Float32}(undef, 2 * num_range_bearings, num_dim_state) # Jacobian matrix ∂ẑ/∂(rx,ry)
	zs, ẑs = [], []  # true and predicted RangeBearings

    for (i, range_bearing) in enumerate(range_bearings)
		mid = range_bearing.landmark_id
        if ismissing(belief.mean[2*mid+2])
			# Initialize its pose in mu based on the measurement and the current robot pose
			mx, my = range_bearing_model([rx, ry, rθ], range_bearing)
			belief.mean[2*mid+2:2*mid+3] = [mx, my]
        end
		# Add the landmark measurement to the Z vector
		zs = [zs; range_bearing.range; range_bearing.bearing]

		# Use the current estimate of the landmark pose
		# to compute the corresponding expected measurement in z̄:
		mx, my = belief.mean[2*mid+2:2*mid+3]
		δ = [mx - rx, my - ry]
		q = dot(δ, δ)
		sqrtq = sqrt(q)

	 	ẑs = [ẑs; sqrtq; atan(δ[2], δ[1]) - rθ]

		# Compute the Jacobian Hi of the measurement function h for this RangeBearing
		δx, δy = δ
		Hi = zeros(Float32, 2, num_dim_state)
		Hi[1:2, 1:3] = [
			-sqrtq * δx  -sqrtq * δy   0;
			δy           -δx           -q
		] / q
		Hi[1:2, 2*mid+2:2*mid+3] = [
			sqrtq * δx sqrtq * δy;
			-δy δx
		] / q

		# Augment H with the new Hi
		H[2*i-1:2*i, 1:end] = Hi
    end

	# Construct the sensor noise matrix Q
	Q = Diagonal{Float32}(ones(2 * num_range_bearings) * 0.01)

	# Compute the Kalman gain K
	K = belief.covariance * H' * inv(H * belief.covariance * H' + Q)

	# Compute the difference between the expected and recorded measurements.
	Δz = zs - ẑs
	# Normalize the bearings
	Δz[2:2:end] = map(bearing->rem2pi(bearing, RoundNearest), Δz[2:2:end])

	# Finish the correction step by computing the new mu and sigma.
	belief.mean += K * Δz
	I = Diagonal{Float32}(ones(num_dim_state))
	belief.covariance = Symmetric((I - K * H) * belief.covariance)

	# Normalize theta in the robot pose.
	belief.mean[3] = rem2pi(belief.mean[3], RoundNearest)
end


## Demo

In [ ]:
include("../src/SlamTutorial.jl")
import .SlamTutorial: 
    Odometry, standard_odometry_model, RangeBearing, range_bearing_model,
    Belief, belief_init, prediction_step, correction_step,
    make_canvas, make_animation, draw_2d_robot, draw_2d_gaussian, draw_kalman_state, animate_kalman_state,
    example2d_landmarks, example2d_sensor_data


In [6]:
landmarks = example2d_landmarks()
num_landmarks = size(landmarks, 1)

odometries, range_bearingss = example2d_sensor_data()

believes = []

belief = belief_init(num_landmarks)
for t in 1:100
    prediction_step(belief, odometries[t])
    correction_step(belief, range_bearingss[t])
    push!(believes, deepcopy(belief))
end


canvas = make_canvas(-1, -1, 11, 11)
HTML(animate_kalman_state(canvas, believes, range_bearingss, landmarks).to_jshtml())

HTML{String}("\n<link rel=\"stylesheet\"\nhref=\"https://maxcdn.bootstrapcdn.com/font-awesome/4.4.0/\ncss/font-awesome.min.css\">\n<script language=\"javascript\">\n  function isInternetExplorer() {\n    ua = navigator.userAgent;\n    /* MSIE used to detect old browsers and Trident used to newer ones*/\n    return ua.indexOf(\"MSIE \") > -1 || ua.indexOf(\"Trident/\") > -1;\n  }\n\n  /* Define the Animation class */\n  function Animation(frames, img_id, slider_id, interval, loop_select_id){\n    this.img_id = img_id;\n    this.slider_id = slider_id;\n    this.loop_select_id = loop_select_id;\n    this.interval = interval;\n    this.current_frame = 0;\n    this.direction = 0;\n    this.timer = null;\n    this.frames = new Array(frames.length);\n\n    for (var i=0; i<frames.length; i++)\n    {\n     this.frames[i] = new Image();\n     this.frames[i].src = frames[i];\n    }\n    var slider = document.getElementById(this.slider_id);\n    slider.max = this.frames.length - 1;\n    if (isInternetExplorer()) {\n        // switch from oninput to onchange because IE <= 11 does not conform\n        // with W3C specification. It ignores oninput and onchange behaves\n        // like oninput. In contrast, Mircosoft Edge behaves correctly.\n        slider.setAttribute('onchange', slider.getAttribute('oninput'));\n        slider.setAttribute('oninput', null);\n    }\n    this.set_frame(this.current_frame);\n  }\n\n  Animation.prototype.get_loop_state = function(){\n    var button_group = document[this.loop_select_id].state;\n    for (var i = 0; i < button_group.length; i++) {\n        var button = button_group[i];\n        if (button.checked) {\n            return button.value;\n        }\n    }\n    return undefined;\n  }\n\n  Animation.prototype.set_frame = function(frame){\n    this.current_frame = frame;\n    document.getElementById(this.img_id).src =\n            this.frames[this.current_frame].src;\n    document.getElementById(this.slider_id).value = this.current_frame;\n  }\n\n  Animation.prototype.next_frame = function()\n  {\n    this.set_frame(Math.min(this.frames.length - 1, this.current_frame + 1));\n  }\n\n  Animation.prototype.previous_frame = function()\n  {\n    this.set_frame(Math.max(0, this.current_frame - 1));\n  }\n\n  Animation.prototype.first_frame = function()\n  {\n    this.set_frame(0);\n  }\n\n  Animation.prototype.last_frame = function()\n  {\n    this.set_frame(this.frames.length - 1);\n  }\n\n  Animation.prototype.slower = function()\n  {\n    this.interval /= 0.7;\n    if(this.direction > 0){this.play_animation();}\n    else if(this.direction < 0){this.reverse_animation();}\n  }\n\n  Animation.prototype.faster = function()\n  {\n    this.interval *= 0.7;\n    if(this.direction > 0){this.play_animation();}\n    else if(this.direction < 0){this.reverse_animation();}\n  }\n\n  Animation.prototype.anim_step_forward = function()\n  {\n    this.current_frame += 1;\n    if(this.current_frame < this.frames.length){\n      this.set_frame(this.current_frame);\n    }else{\n      var loop_state = this.get_loop_state();\n      if(loop_state == \"loop\"){\n        this.first_frame();\n      }else if(loop_state == \"reflect\"){\n        this.last_frame();\n        this.reverse_animation();\n      }else{\n        this.pause_animation();\n        this.last_frame();\n      }\n    }\n  }\n\n  Animation.prototype.anim_step_reverse = function()\n  {\n    this.current_frame -= 1;\n    if(this.current_frame >= 0){\n      this.set_frame(this.current_frame);\n    }else{\n      var loop_state = this.get_loop_state();\n      if(loop_state == \"loop\"){\n        this.last_frame();\n      }else if(loop_state == \"reflect\"){\n        this.first_frame();\n        this.play_animation();\n      }else{\n        this.pause_animation();\n        this.first_frame();\n      }\n    }\n  }\n\n  Animation.prototype.pause_animation = function()\n  {\n    this.direction = 0;\n    if (this.timer){\n      clearInterval(this.timer);\n      this.timer = nul